In [1]:
import tensorflow as tf

gpus = tf.config.list_physical_devices("GPU")

if gpus:
    tf.config.experimental.set_memory_growth(gpus[0], True)  #设置GPU显存用量按需使用
    tf.config.set_visible_devices([gpus[0]],"GPU")
    
# 打印显卡信息，确认GPU可用
print(gpus)

[PhysicalDevice(name='/physical_device:GPU:0', device_type='GPU')]


In [2]:
from tensorflow.keras import layers, datasets, Sequential, Model, optimizers
from tensorflow.keras.layers import LeakyReLU, UpSampling2D, Conv2D

import matplotlib.pyplot as plt
import numpy             as np
import sys,os,pathlib

# 定义训练参数
img_shape  = (28, 28, 1)
latent_dim = 200

## 构建生成器

In [3]:
def build_generator():
    # ======================================= #
    #     生成器，输入一串随机数字生成图片
    # ======================================= #
    model = Sequential([
        layers.Dense(256, input_dim=latent_dim),
        layers.LeakyReLU(alpha=0.2),               # 高级一点的激活函数
        layers.BatchNormalization(momentum=0.8),   # BN 归一化
        
        layers.Dense(512),
        layers.LeakyReLU(alpha=0.2),
        layers.BatchNormalization(momentum=0.8),
        
        layers.Dense(1024),
        layers.LeakyReLU(alpha=0.2),
        layers.BatchNormalization(momentum=0.8),
        
        layers.Dense(np.prod(img_shape), activation='tanh'),
        layers.Reshape(img_shape)
    ])

    noise = layers.Input(shape=(latent_dim,))
    img = model(noise)

    return Model(noise, img)

## 构建鉴别器

In [4]:
def build_discriminator():
    # ===================================== #
    #   鉴别器，对输入的图片进行判别真假
    # ===================================== #
    model = Sequential([
        layers.Flatten(input_shape=img_shape),
        layers.Dense(512),
        layers.LeakyReLU(alpha=0.2),
        layers.Dense(256),
        layers.LeakyReLU(alpha=0.2),
        layers.Dense(1, activation='sigmoid')
    ])

    img = layers.Input(shape=img_shape)
    validity = model(img)

    return Model(img, validity)

In [5]:
# 创建判别器
discriminator = build_discriminator()
# 定义优化器
optimizer = tf.keras.optimizers.Adam(1e-4)
discriminator.compile(loss='binary_crossentropy',
                      optimizer=optimizer,
                      metrics=['accuracy'])

# 创建生成器 
generator = build_generator()
gan_input = layers.Input(shape=(latent_dim,))
img = generator(gan_input)

# 在训练generate的时候不训练discriminator
discriminator.trainable = False

# 对生成的假图片进行预测
validity = discriminator(img)
combined = Model(gan_input, validity)
combined.compile(loss='binary_crossentropy', optimizer=optimizer)


In [20]:
discriminator

In [21]:
generator

In [26]:
gan_input

<KerasTensor: shape=(None, 200) dtype=float32 (created by layer 'input_3')>

In [25]:
gan_input.shape

TensorShape([None, 200])

In [23]:
validity

<KerasTensor: shape=(None, 1) dtype=float32 (created by layer 'model')>

In [24]:
combined

In [27]:
img

<KerasTensor: shape=(None, 28, 28, 1) dtype=float32 (created by layer 'model_1')>

## 保存样例图片

In [6]:
def sample_images(epoch):
    """
    保存样例图片
    """
    row, col = 4, 4
    noise = np.random.normal(0, 1, (row*col, latent_dim))
    gen_imgs = generator.predict(noise)

    fig, axs = plt.subplots(row, col)
    cnt = 0
    for i in range(row):
        for j in range(col):
            axs[i,j].imshow(gen_imgs[cnt, :,:,0], cmap='gray')
            axs[i,j].axis('off')
            cnt += 1
    fig.savefig("images/%05d.png" % epoch)
    plt.close()

## 训练模型

In [7]:
def train(epochs, batch_size=128, sample_interval=50):
    # 加载数据
    # 文件位置：C:\Users\HP ZBook15\.keras\datasets
    (train_images,_), (_,_) = tf.keras.datasets.mnist.load_data()

    # 将图片标准化到 [-1, 1] 区间内   
    train_images = (train_images - 127.5) / 127.5
    # 数据
    train_images = np.expand_dims(train_images, axis=3)

    # 创建标签
    true = np.ones((batch_size, 1))
    fake = np.zeros((batch_size, 1))
    
    # 进行循环训练
    for epoch in range(epochs): 

        # 随机选择 batch_size 张图片
        idx = np.random.randint(0, train_images.shape[0], batch_size)
        imgs = train_images[idx]      
        
        # 生成噪音
        noise = np.random.normal(0, 1, (batch_size, latent_dim))
        # 生成器通过噪音生成图片，gen_imgs的shape为：(128, 28, 28, 1)
        gen_imgs = generator.predict(noise)
        
        # 训练鉴别器 
        d_loss_true = discriminator.train_on_batch(imgs, true)
        d_loss_fake = discriminator.train_on_batch(gen_imgs, fake)
        # 返回loss值
        d_loss = 0.5 * np.add(d_loss_true, d_loss_fake)

        # 训练生成器
        noise = np.random.normal(0, 1, (batch_size, latent_dim))
        g_loss = combined.train_on_batch(noise, true)
        
        print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))

        # 保存样例图片
        if epoch % sample_interval == 0:
            sample_images(epoch)

In [8]:
train(epochs=50000, batch_size=512, sample_interval=500)

16/16 [==============================] - 1s 3ms/step
0 [D loss: 0.564433, acc.: 55.57%] [G loss: 0.615958]
16/16 [==============================] - 0s 2ms/step
1 [D loss: 0.428365, acc.: 61.04%] [G loss: 0.601898]
16/16 [==============================] - 0s 2ms/step
2 [D loss: 0.390525, acc.: 64.84%] [G loss: 0.629429]
16/16 [==============================] - 0s 2ms/step
3 [D loss: 0.376864, acc.: 69.53%] [G loss: 0.637371]
16/16 [==============================] - 0s 2ms/step
4 [D loss: 0.368233, acc.: 70.31%] [G loss: 0.672757]
16/16 [==============================] - 0s 2ms/step
5 [D loss: 0.353537, acc.: 74.02%] [G loss: 0.707676]
16/16 [==============================] - 0s 2ms/step
6 [D loss: 0.343984, acc.: 78.52%] [G loss: 0.762580]
16/16 [==============================] - 0s 2ms/step
7 [D loss: 0.322071, acc.: 83.79%] [G loss: 0.827754]
16/16 [==============================] - 0s 2ms/step
8 [D loss: 0.305846, acc.: 86.04%] [G loss: 0.892810]
16/16 [==============================

16/16 [==============================] - 0s 2ms/step
75 [D loss: 0.018106, acc.: 100.00%] [G loss: 3.663338]
16/16 [==============================] - 0s 2ms/step
76 [D loss: 0.019914, acc.: 100.00%] [G loss: 3.688024]
16/16 [==============================] - 0s 2ms/step
77 [D loss: 0.019756, acc.: 100.00%] [G loss: 3.701526]
16/16 [==============================] - 0s 2ms/step
78 [D loss: 0.018645, acc.: 100.00%] [G loss: 3.741901]
16/16 [==============================] - 0s 2ms/step
79 [D loss: 0.017600, acc.: 100.00%] [G loss: 3.748568]
16/16 [==============================] - 0s 2ms/step
80 [D loss: 0.018133, acc.: 100.00%] [G loss: 3.720729]
16/16 [==============================] - 0s 2ms/step
81 [D loss: 0.018748, acc.: 100.00%] [G loss: 3.746295]
16/16 [==============================] - 0s 2ms/step
82 [D loss: 0.017019, acc.: 100.00%] [G loss: 3.792322]
16/16 [==============================] - 0s 2ms/step
83 [D loss: 0.018266, acc.: 100.00%] [G loss: 3.822839]
16/16 [============

16/16 [==============================] - 0s 2ms/step
150 [D loss: 0.027305, acc.: 99.80%] [G loss: 4.171447]
16/16 [==============================] - 0s 2ms/step
151 [D loss: 0.025106, acc.: 99.90%] [G loss: 4.201185]
16/16 [==============================] - 0s 2ms/step
152 [D loss: 0.025974, acc.: 100.00%] [G loss: 4.136949]
16/16 [==============================] - 0s 2ms/step
153 [D loss: 0.029572, acc.: 99.90%] [G loss: 4.167675]
16/16 [==============================] - 0s 2ms/step
154 [D loss: 0.024343, acc.: 99.90%] [G loss: 4.113206]
16/16 [==============================] - 0s 2ms/step
155 [D loss: 0.027663, acc.: 99.90%] [G loss: 4.088719]
16/16 [==============================] - 0s 2ms/step
156 [D loss: 0.028314, acc.: 100.00%] [G loss: 4.059196]
16/16 [==============================] - 0s 2ms/step
157 [D loss: 0.033433, acc.: 99.71%] [G loss: 4.052761]
16/16 [==============================] - 0s 2ms/step
158 [D loss: 0.029891, acc.: 99.90%] [G loss: 4.106848]
16/16 [==========

16/16 [==============================] - 0s 2ms/step
225 [D loss: 0.098092, acc.: 97.17%] [G loss: 3.650225]
16/16 [==============================] - 0s 1ms/step
226 [D loss: 0.089054, acc.: 98.05%] [G loss: 3.647479]
16/16 [==============================] - 0s 2ms/step
227 [D loss: 0.097120, acc.: 97.27%] [G loss: 3.526895]
16/16 [==============================] - 0s 2ms/step
228 [D loss: 0.086201, acc.: 97.75%] [G loss: 3.634149]
16/16 [==============================] - 0s 2ms/step
229 [D loss: 0.091159, acc.: 97.66%] [G loss: 3.560234]
16/16 [==============================] - 0s 2ms/step
230 [D loss: 0.085601, acc.: 98.44%] [G loss: 3.742160]
16/16 [==============================] - 0s 2ms/step
231 [D loss: 0.094096, acc.: 97.46%] [G loss: 3.740523]
16/16 [==============================] - 0s 2ms/step
232 [D loss: 0.095540, acc.: 97.95%] [G loss: 3.755325]
16/16 [==============================] - 0s 2ms/step
233 [D loss: 0.094959, acc.: 98.14%] [G loss: 3.649151]
16/16 [============

16/16 [==============================] - 0s 2ms/step
300 [D loss: 0.024817, acc.: 99.71%] [G loss: 4.867555]
16/16 [==============================] - 0s 2ms/step
301 [D loss: 0.023446, acc.: 100.00%] [G loss: 5.043087]
16/16 [==============================] - 0s 2ms/step
302 [D loss: 0.019244, acc.: 99.90%] [G loss: 5.044683]
16/16 [==============================] - 0s 2ms/step
303 [D loss: 0.022913, acc.: 99.80%] [G loss: 5.026663]
16/16 [==============================] - 0s 2ms/step
304 [D loss: 0.019541, acc.: 100.00%] [G loss: 5.126045]
16/16 [==============================] - 0s 2ms/step
305 [D loss: 0.019467, acc.: 100.00%] [G loss: 5.153867]
16/16 [==============================] - 0s 2ms/step
306 [D loss: 0.019584, acc.: 99.80%] [G loss: 5.226294]
16/16 [==============================] - 0s 2ms/step
307 [D loss: 0.017635, acc.: 100.00%] [G loss: 5.228654]
16/16 [==============================] - 0s 2ms/step
308 [D loss: 0.019704, acc.: 99.90%] [G loss: 5.155229]
16/16 [========

...

16/16 [==============================] - 0s 2ms/step
49641 [D loss: 0.718557, acc.: 48.63%] [G loss: 0.786407]
16/16 [==============================] - 0s 2ms/step
49642 [D loss: 0.709872, acc.: 50.29%] [G loss: 0.784079]
16/16 [==============================] - 0s 2ms/step
49643 [D loss: 0.711604, acc.: 51.17%] [G loss: 0.762912]
16/16 [==============================] - 0s 2ms/step
49644 [D loss: 0.708776, acc.: 50.39%] [G loss: 0.768107]
16/16 [==============================] - 0s 2ms/step
49645 [D loss: 0.690407, acc.: 52.25%] [G loss: 0.780449]
16/16 [==============================] - 0s 2ms/step
49646 [D loss: 0.709617, acc.: 50.49%] [G loss: 0.779013]
16/16 [==============================] - 0s 2ms/step
49647 [D loss: 0.705938, acc.: 50.78%] [G loss: 0.793378]
16/16 [==============================] - 0s 2ms/step
49648 [D loss: 0.697782, acc.: 52.54%] [G loss: 0.784213]
16/16 [==============================] - 0s 2ms/step
49649 [D loss: 0.690549, acc.: 53.71%] [G loss: 0.795150]
1

16/16 [==============================] - 0s 2ms/step
49715 [D loss: 0.696742, acc.: 50.98%] [G loss: 0.771645]
16/16 [==============================] - 0s 2ms/step
49716 [D loss: 0.678384, acc.: 56.05%] [G loss: 0.771766]
16/16 [==============================] - 0s 2ms/step
49717 [D loss: 0.693356, acc.: 53.61%] [G loss: 0.792123]
16/16 [==============================] - 0s 2ms/step
49718 [D loss: 0.689100, acc.: 54.00%] [G loss: 0.790686]
16/16 [==============================] - 0s 2ms/step
49719 [D loss: 0.691535, acc.: 51.76%] [G loss: 0.789660]
16/16 [==============================] - 0s 2ms/step
49720 [D loss: 0.691137, acc.: 55.37%] [G loss: 0.809447]
16/16 [==============================] - 0s 2ms/step
49721 [D loss: 0.717542, acc.: 49.02%] [G loss: 0.790781]
16/16 [==============================] - 0s 2ms/step
49722 [D loss: 0.694082, acc.: 54.00%] [G loss: 0.785899]
16/16 [==============================] - 0s 2ms/step
49723 [D loss: 0.697061, acc.: 53.32%] [G loss: 0.781097]
1

16/16 [==============================] - 0s 2ms/step
49789 [D loss: 0.684682, acc.: 54.69%] [G loss: 0.766205]
16/16 [==============================] - 0s 2ms/step
49790 [D loss: 0.695979, acc.: 51.95%] [G loss: 0.761453]
16/16 [==============================] - 0s 2ms/step
49791 [D loss: 0.694457, acc.: 52.44%] [G loss: 0.790322]
16/16 [==============================] - 0s 2ms/step
49792 [D loss: 0.700643, acc.: 51.56%] [G loss: 0.779625]
16/16 [==============================] - 0s 2ms/step
49793 [D loss: 0.697182, acc.: 51.95%] [G loss: 0.806359]
16/16 [==============================] - 0s 2ms/step
49794 [D loss: 0.694857, acc.: 53.42%] [G loss: 0.802490]
16/16 [==============================] - 0s 2ms/step
49795 [D loss: 0.683955, acc.: 55.37%] [G loss: 0.794608]
16/16 [==============================] - 0s 2ms/step
49796 [D loss: 0.696882, acc.: 52.93%] [G loss: 0.785666]
16/16 [==============================] - 0s 2ms/step
49797 [D loss: 0.702760, acc.: 51.46%] [G loss: 0.785482]
1

16/16 [==============================] - 0s 2ms/step
49863 [D loss: 0.696539, acc.: 53.42%] [G loss: 0.793755]
16/16 [==============================] - 0s 2ms/step
49864 [D loss: 0.694294, acc.: 52.34%] [G loss: 0.783380]
16/16 [==============================] - 0s 2ms/step
49865 [D loss: 0.695521, acc.: 53.42%] [G loss: 0.787076]
16/16 [==============================] - 0s 2ms/step
49866 [D loss: 0.701160, acc.: 51.56%] [G loss: 0.779046]
16/16 [==============================] - 0s 2ms/step
49867 [D loss: 0.702849, acc.: 51.66%] [G loss: 0.789014]
16/16 [==============================] - 0s 2ms/step
49868 [D loss: 0.691618, acc.: 54.00%] [G loss: 0.793621]
16/16 [==============================] - 0s 2ms/step
49869 [D loss: 0.691383, acc.: 54.59%] [G loss: 0.775977]
16/16 [==============================] - 0s 2ms/step
49870 [D loss: 0.700492, acc.: 50.98%] [G loss: 0.792557]
16/16 [==============================] - 0s 2ms/step
49871 [D loss: 0.691857, acc.: 52.93%] [G loss: 0.792176]
1

16/16 [==============================] - 0s 2ms/step
49937 [D loss: 0.696660, acc.: 53.22%] [G loss: 0.806514]
16/16 [==============================] - 0s 2ms/step
49938 [D loss: 0.693549, acc.: 52.83%] [G loss: 0.797284]
16/16 [==============================] - 0s 2ms/step
49939 [D loss: 0.686064, acc.: 53.91%] [G loss: 0.793601]
16/16 [==============================] - 0s 2ms/step
49940 [D loss: 0.692826, acc.: 55.08%] [G loss: 0.775102]
16/16 [==============================] - 0s 2ms/step
49941 [D loss: 0.703555, acc.: 51.07%] [G loss: 0.781580]
16/16 [==============================] - 0s 2ms/step
49942 [D loss: 0.695220, acc.: 51.76%] [G loss: 0.778782]
16/16 [==============================] - 0s 2ms/step
49943 [D loss: 0.691297, acc.: 54.59%] [G loss: 0.784575]
16/16 [==============================] - 0s 2ms/step
49944 [D loss: 0.692472, acc.: 50.49%] [G loss: 0.786797]
16/16 [==============================] - 0s 2ms/step
49945 [D loss: 0.695972, acc.: 52.64%] [G loss: 0.783068]
1

In [19]:
Model.save('model')

TypeError: save() missing 1 required positional argument: 'filepath'

In [12]:
import imageio

def compose_gif():
    # 图片地址
    data_dir = r"E:\demo_study\jupyter\Jupyter_notebook\Handwritten-numeral-generation-based-on-GAN\images"
    data_dir = pathlib.Path(data_dir)
    paths    = list(data_dir.glob('*'))
    
    gif_images = []
    for path in paths:
#         print(path)
        gif_images.append(imageio.imread(path))
    imageio.mimsave("test.gif",gif_images,fps=10)
    
compose_gif()